In [11]:
import sklearn
sklearn.__version__
import pandas as pd  
import time
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split, RepeatedKFold, GridSearchCV, cross_val_score
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import SimpleImputer
from sklearn.impute import KNNImputer
import numpy as np
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, BaggingClassifier, VotingClassifier, ExtraTreesClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
import lightgbm as lgb
from sklearn.ensemble import StackingClassifier
from sklearn.pipeline import Pipeline
from sklearn.ensemble import BaggingClassifier
from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from sklearn.linear_model import LogisticRegression  # Added logistic regression


In [12]:
# Load the training and test data
sample = pd.read_csv('train.csv')
testdatax= pd.read_csv('test.csv')

# Remove columns with 'noninvasive' in their names
text_to_find = 'noninvasive'
columns_to_drop = [col for col in sample.columns if text_to_find in col]
sample.drop(columns=columns_to_drop, inplace=True)
columns_to_drop = [col for col in testdatax.columns if text_to_find in col]
testdatax.drop(columns=columns_to_drop, inplace=True)

# Select columns by data type
ob_col = sample.select_dtypes(include=['object']).columns
not_ob_col = sample.select_dtypes(exclude=['object']).columns
not_ob_col_age = sample.select_dtypes(exclude=['object']).columns

# Delete the last column from not_ob_col_age
not_ob_col_age.delete([-1])

# Initialize a RobustScaler
scaler = RobustScaler()
# Scale numerical columns
for i in not_ob_col:
    sample[i] = scaler.fit_transform(sample[i].values.reshape(-1, 1))

not_ob_col_test = testdatax.select_dtypes(exclude=['object']).columns

# Delete the first column from not_ob_col_test
not_ob_col_test.delete(0)

# Scale numerical columns in the test data
for i in not_ob_col_test:
    testdatax[i] = scaler.fit_transform(testdatax[i].values.reshape(-1, 1))

# Perform one-hot encoding on the test data and training data
df_onehot_test = pd.get_dummies(testdatax)
df_onehot_sample = pd.get_dummies(sample)

# Separate features (X) and target variable (y)
X = df_onehot_sample.iloc[:, df_onehot_sample.columns != 'hospital_death']
y = df_onehot_sample['hospital_death']


In [13]:
def fit_model(model, model_name):
    model.fit(trainX, trainy)
    md_probs = model.predict_proba(test_2X)
    md_probs = md_probs[:, 1]
    md_auc = roc_auc_score(testy, md_probs)
    print(model_name, " : ", md_auc)


In [14]:
# Split the data into training and testing sets
trainX, test_2X, trainy, testy = train_test_split(X, y, test_size=0.3, random_state=2)


In [15]:
Bg_xgb = BaggingClassifier(base_estimator=XGBClassifier(max_depth=3, n_estimators=500, learning_rate=0.1, n_jobs=-1, reg_lambda=0.8, reg_alpha=0.9, subsample=0.8, colsample_bytree=0.9, boosting_type='gbdt', num_leaves=10), n_estimators=100, n_jobs=-1, warm_start=True)

# Fit and evaluate the BaggingClassifier with XGBoost
fit_model(Bg_xgb, "Bagging Classifier (XGBoost)")


/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:52:12] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:52:12] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:52:12] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


Bagging Classifier (XGBoost)  :  0.8884163737203498


In [16]:
# Initialize a BaggingClassifier with LightGBM as the base estimator
Bg_lgbm = BaggingClassifier(base_estimator=LGBMClassifier(n_estimators=500, random_state=42, learning_rate=0.1, max_depth=3, boosting_type='gbdt', colsample_bytree=0.8, subsample=0.8, reg_alpha=0.9, reg_lambda=0.8, n_jobs=-1, num_leaves=10), n_estimators=100, n_jobs=-1, warm_start=True)
# Fit and evaluate the BaggingClassifier with LightGBM
fit_model(Bg_lgbm, "Bagging Classifier (LightGBM)")

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


[LightGBM] [Info] Number of positive: 3057, number of negative: 31943
[LightGBM] [Info] Number of positive: 3057, number of negative: 31943
[LightGBM] [Info] Number of positive: 3057, number of negative: 31943
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.014409 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3955
[LightGBM] [Info] Number of data points in the train set: 35000, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.088171 -> initscore=-2.336169
[LightGBM] [Info] Start training from score -2.336169
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004124 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3955
[LightGBM] [Info] Number of data points in 

In [17]:
# Define XGBoost parameters
xgb_params = {
    'learning_rate': 0.1,
    'max_depth': 3,
    'boosting_type': 'gbdt',
    'colsample_bytree': 0.8,
    'subsample': 0.8,
    'reg_alpha': 0.9,
    'reg_lambda': 0.8,
    'n_jobs': -1,
    'num_leaves': 10
}

# Create an XGBoostClassifier as the base estimator for stacking
base_xgb_model = XGBClassifier(n_estimators=500, random_state=42, **xgb_params)

# Create a BaggingClassifier with XGBoost as the base estimator and warm start enabled
Bg_xgb = BaggingClassifier(base_estimator=base_xgb_model, n_estimators=215, random_state=42, warm_start=True)

# Fit the BaggingClassifier with XGBoost
Bg_xgb.fit(X, y)


/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:53:52] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:53:54] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [20:53:56] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


BaggingClassifier(base_estimator=XGBClassifier(base_score=None, booster=None,
                                               boosting_type='gbdt',
                                               callbacks=None,
                                               colsample_bylevel=None,
                                               colsample_bynode=None,
                                               colsample_bytree=0.8,
                                               device=None,
                                               early_stopping_rounds=None,
                                               enable_categorical=False,
                                               eval_metric=None,
                                               feature_types=None, gamma=None,
                                               grow_policy=None,
                                               importance_type=None,
                                               interaction_constraints=None,
                                               learning_rate=0.1, max_bin=None,
                                               max_cat_threshold=None,
                                               max_cat_to_onehot=None,
                                               max_delta_step=None, max_depth=3,
                                               max_leaves=None,
                                               min_child_weight=None,
                                               missing=nan,
                                               monotone_constraints=None,
                                               multi_strategy=None,
                                               n_estimators=500, n_jobs=-1,
                                               num_leaves=10, ...),
                  n_estimators=215, random_state=42, warm_start=True)

In [18]:
# Initialize a BaggingClassifier with LightGBM as the base estimator for stacking
base_lgbm_model = LGBMClassifier(n_estimators=500, random_state=42, learning_rate=0.1, max_depth=3, boosting_type='gbdt', colsample_bytree=0.8, subsample=0.8, reg_alpha=0.9, reg_lambda=0.8, n_jobs=-1, num_leaves=10)

# Create a BaggingClassifier with LightGBM as the base estimator and warm start enabled
Bg_lgbm = BaggingClassifier(base_estimator=base_lgbm_model, n_estimators=215, random_state=42, warm_start=True)



In [19]:
# Fit the BaggingClassifier with LightGBM
Bg_lgbm.fit(X, y)

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


[LightGBM] [Info] Number of positive: 4338, number of negative: 45662
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004430 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4009
[LightGBM] [Info] Number of data points in the train set: 50000, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.089600 -> initscore=-2.318529
[LightGBM] [Info] Start training from score -2.318529
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

BaggingClassifier(base_estimator=LGBMClassifier(colsample_bytree=0.8,
                                                max_depth=3, n_estimators=500,
                                                n_jobs=-1, num_leaves=10,
                                                random_state=42, reg_alpha=0.9,
                                                reg_lambda=0.8, subsample=0.8),
                  n_estimators=215, random_state=42, warm_start=True)

In [20]:
# Make predictions on the test data using the BaggingClassifiers
md_probs_xgb = Bg_xgb.predict_proba(df_onehot_test)[:, 1]
md_probs_lgbm = Bg_lgbm.predict_proba(df_onehot_test)[:, 1]

In [21]:
# Create DataFrames with predictions and record IDs
df_xgb = pd.DataFrame(md_probs_xgb)
df_lgbm = pd.DataFrame(md_probs_lgbm)
custom_starting_index = 50001
df_xgb.insert(0, 'RecordID', range(custom_starting_index, custom_starting_index + len(df_xgb)))
df_lgbm.insert(0, 'RecordID', range(custom_starting_index, custom_starting_index + len(df_lgbm)))

custom_column_names_xgb = ['RecordID', 'hospital_death']
custom_column_names_lgbm = ['RecordID', 'hospital_death']


In [22]:
# Specify the file paths for saving the predictions CSV files
csv_file_path_xgb = 'predict_xgb_bagging.csv'
csv_file_path_lgbm = 'predict_lgbm_bagging.csv'


In [23]:
# Save the predictions to CSV files
df_xgb.to_csv(csv_file_path_xgb, index=False, header=custom_column_names_xgb)
df_lgbm.to_csv(csv_file_path_lgbm, index=False, header=custom_column_names_lgbm)


In [25]:
# Create a stacking classifier with the BaggingClassifiers as base estimators
estimators = [
    ('xgb', Bg_xgb),    # Bagged XGBoost as the first base estimator
    ('lgbm', Bg_lgbm),  # Bagged LightGBM as the second base estimator
]

stacking_model = StackingClassifier(
    estimators=estimators,
    final_estimator=LogisticRegression()  # Logistic Regression as the final estimator
)


In [27]:
# Fit the stacking model on the training data
stacking_model.fit(X, y)


/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:40:28] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:40:30] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:40:31] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


[LightGBM] [Info] Number of positive: 4338, number of negative: 45662
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004230 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4009
[LightGBM] [Info] Number of data points in the train set: 50000, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.089600 -> initscore=-2.318529
[LightGBM] [Info] Start training from score -2.318529
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:49:20] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:49:22] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/xgboost/core.py:160: UserWarning: [21:49:23] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "boosting_type", "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


[LightGBM] [Info] Number of positive: 3471, number of negative: 36529
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003649 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3966
[LightGBM] [Info] Number of data points in the train set: 40000, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.083700 -> initscore=-2.393105
[LightGBM] [Info] Start training from score -2.393105
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


[LightGBM] [Info] Number of positive: 3471, number of negative: 36529
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003323 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3977
[LightGBM] [Info] Number of data points in the train set: 40000, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.085625 -> initscore=-2.368263
[LightGBM] [Info] Start training from score -2.368263
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

KeyboardInterrupt: 

In [ ]:
# Make predictions on the test data using the stacking model
stacking_predictions = stacking_model.predict_proba(df_onehot_test)[:, 1]

# Create a DataFrame with stacking model predictions and record IDs
df_stacking_predictions = pd.DataFrame(stacking_predictions, columns=['hospital_death'])
df_stacking_predictions.insert(0, 'RecordID', range(custom_starting_index, custom_starting_index + len(df_stacking_predictions)))

# Specify the file path for saving the stacking model predictions CSV file
stacking_csv_file_path = 'prediction_stacking.csv'

# Save the stacking model predictions to a CSV file
df_stacking_predictions.to_csv(stacking_csv_file_path, index=False)